In [37]:
#%%
from datetime import datetime
from importlib import reload
from vnpy.app.portfolio_strategy import BacktestingEngine
from vnpy.trader.constant import Interval

symbols = {
    "SHFE": ["CU", "AL", "ZN", "PB", "NI", "SN", "AU", "AG", "RB", "HC", "BU", "RU",],
    "DCE": ["C", "CS", "A", "B", "M", "Y", "P", "BB", "JD", "L", "V", "PP", "J", "JM", "I"],
    "CZCE": ["SR", "CF", "CY", "PM","WH", "RI", "LR", "JR","OI", "RS", "RM", "TA", "MA", "FG", "SF", "ZC", "SM"],
}
contract_type = "99"  # 99代表指数合约

In [38]:
def generate_all_vt_symbols(symbols, contract_type):
    """
    合成回测用的vt_symbol列表
    vt_symbol 格式：合约代码.交易所 （ej：AG99.SHFE）
    """
    vt_symbols = []
    for k, v in symbols.items():
        for i in v:
            symbol = i + contract_type + "." + k
            vt_symbols.append(symbol)
    return vt_symbols

In [39]:
def set_ratios(num, vt_symbols):
    """
    设置每个vt_symbol的回测参数,最终返回字典格式
    用于设置手续费，滑点，合约规模，price tick
    """
    d = {}
    for i in vt_symbols:
        d[i] = num
    return d

In [40]:
def show_result(
    vt_symbols,
    strategy,
    setting={},
    show_chart=True
):
    # 1）创建回测引擎对象
    engine = BacktestingEngine()
    # 2）设置回测参数
    engine.set_parameters(
        vt_symbols=vt_symbols,
        interval=Interval.DAILY,
        start=datetime(2006, 1, 1),
        end=datetime(2020, 12, 30),
        rates=set_ratios(1/1000, vt_symbols),  # 设置每个合约的手续费，字典格式
        slippages=set_ratios(0, vt_symbols),  #滑点，字典格式
        sizes=set_ratios(1, vt_symbols),      #合约规模，字典格式
        priceticks=set_ratios(0.01, vt_symbols), #最小价格跳动，字典格式
        capital=5_000_000,
    )
    # 3）添加策略
    engine.add_strategy(strategy, setting)
    # 4）加载历史数据
    engine.load_data()
    # 5）跑回测，基于事件引擎逐条回放，得到成交记录
    engine.run_backtesting()
    # 6）基于逐日盯市规则和成交记录，得到组合资金曲线
    df = engine.calculate_result()
    # 7）基于资金曲线，计算策略回测指标，如收益率，夏普比率
    engine.calculate_statistics()
    # 8）画图
    if show_chart:
        engine.show_chart()

In [41]:
# 生成可交易合约
all_vt_symbols = generate_all_vt_symbols(symbols, contract_type)

In [43]:
# 加载策略，一键回测
import return10_strategy
reload(return10_strategy)
show_result(all_vt_symbols ,return10_strategy.Return10Strategy)

2021-01-30 20:55:28.164325	开始加载历史数据
2021-01-30 20:55:28.449355	CU99.SHFE历史数据加载完成，数据量：3646
2021-01-30 20:55:28.732356	AL99.SHFE历史数据加载完成，数据量：3646
2021-01-30 20:55:29.229354	ZN99.SHFE历史数据加载完成，数据量：3353
2021-01-30 20:55:29.451360	PB99.SHFE历史数据加载完成，数据量：2379
2021-01-30 20:55:29.620353	NI99.SHFE历史数据加载完成，数据量：1407
2021-01-30 20:55:29.791353	SN99.SHFE历史数据加载完成，数据量：1407
2021-01-30 20:55:30.048324	AU99.SHFE历史数据加载完成，数据量：3158
2021-01-30 20:55:30.251323	AG99.SHFE历史数据加载完成，数据量：2106
2021-01-30 20:55:30.494352	RB99.SHFE历史数据加载完成，数据量：2863
2021-01-30 20:55:30.672356	HC99.SHFE历史数据加载完成，数据量：1655
2021-01-30 20:55:30.860352	BU99.SHFE历史数据加载完成，数据量：1766
2021-01-30 20:55:31.143355	RU99.SHFE历史数据加载完成，数据量：3646
2021-01-30 20:55:31.424355	C99.DCE历史数据加载完成，数据量：3646
2021-01-30 20:55:31.594352	CS99.DCE历史数据加载完成，数据量：1470
2021-01-30 20:55:31.935351	A99.DCE历史数据加载完成，数据量：3646
2021-01-30 20:55:32.235353	B99.DCE历史数据加载完成，数据量：3646
2021-01-30 20:55:32.515364	M99.DCE历史数据加载完成，数据量：3646
2021-01-30 20:55:32.795355	Y99.DCE历史数据加载完成，数据量：3643
202